### Ablation Study 1 — Baseline 

This baseline runs plain LoRA fine-tuning on the speech-to-speech translation model.
It includes standard audio → text training, no semantic feedback, no confidence filtering, no context memory, no reinforcement or post-processing.
So it will load model + processor, stream audio–text batches, compute loss and backprop, run validation (Loss / BLEU / WER), save best checkpoints
This serves as the **reference model** for comparing all future ablations.


In [2]:
import sys
import os
import json
import logging
from datetime import datetime
from pathlib import Path
import torch
from tqdm.notebook import tqdm
from torch.utils.data import DataLoader
from torch.optim import AdamW
from transformers import get_linear_schedule_with_warmup
from config import config
from dataloader import StreamingDatasetWithContext, collate_fn
from model_setup import load_models
from generation import calculate_wer, calculate_bleu


In [3]:
config.num_epochs = 5
config.checkpoints_dir = "baseline_ablation/checkpoints"
config.logs_dir = "baseline_ablation/logs"

# Ensure target language is set 
if not getattr(config, "target_lang", None):
    config.target_lang = "cym"  # Welsh by default

# Logging setup
for dir_path in [config.checkpoints_dir, config.logs_dir]:
    Path(dir_path).mkdir(parents=True, exist_ok=True)

timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
log_file = Path(config.logs_dir) / f"baseline_{timestamp}.log"
logging.basicConfig(
    level=logging.INFO,
    format="%(asctime)s [%(levelname)s] %(message)s",
    handlers=[logging.FileHandler(log_file, encoding="utf-8"), logging.StreamHandler(sys.stdout)],
)
logger = logging.getLogger("baseline_training")

logger.info("-" * 70)
logger.info("Ablation Study 1 - Baseline Model Training")
logger.info(f"Started: {datetime.now().isoformat()}")
logger.info(f"Target language (tgt_lang): {config.target_lang}")
logger.info("-" * 70)

2025-11-16 11:31:08,065 [INFO] ----------------------------------------------------------------------
2025-11-16 11:31:08,066 [INFO] Ablation Study 1 - Baseline Model Training
2025-11-16 11:31:08,066 [INFO] Started: 2025-11-16T11:31:08.066820
2025-11-16 11:31:08,067 [INFO] Target language (tgt_lang): cym
2025-11-16 11:31:08,068 [INFO] ----------------------------------------------------------------------


In [4]:
class BaselineTrainer:
    def __init__(self):
        logger.info("Loading models...")
        models = load_models()
        self.model = models["s2s_model"]
        self.processor = models["processor"]
        self.model = self.model.to(config.device)
        self.model.eval()
        logger.info("Models loaded and moved to device")

        logger.info("Creating datasets and dataloaders...")
        train_dataset = StreamingDatasetWithContext(split=config.train_split)
        val_dataset = StreamingDatasetWithContext(split=config.val_split)

        # Optionally limit samples if config provides caps
        if getattr(config, "max_train_samples", None):
            logger.info(f"Limiting train samples to {config.max_train_samples}")
        if getattr(config, "max_val_samples", None):
            logger.info(f"Limiting val samples to {config.max_val_samples}")

        self.train_loader = DataLoader(
            train_dataset,
            batch_size=config.batch_size,
            shuffle=True,
            collate_fn=collate_fn,
            drop_last=True,
            num_workers=0,
        )
        self.val_loader = DataLoader(
            val_dataset,
            batch_size=config.batch_size,
            shuffle=False,
            collate_fn=collate_fn,
            num_workers=0,
        )
        logger.info(f"Train batches: {len(self.train_loader)}")
        logger.info(f"Val batches: {len(self.val_loader)}")

        logger.info("Setting up optimizer and scheduler...")
        trainable_params = [p for p in self.model.parameters() if p.requires_grad]
        self.optimizer = AdamW(trainable_params, lr=config.learning_rate, weight_decay=config.weight_decay)
        total_steps = max(1, len(self.train_loader) * config.num_epochs)
        self.scheduler = get_linear_schedule_with_warmup(self.optimizer, config.warmup_steps, total_steps)
        logger.info(f"  Total steps: {total_steps}")

        self.global_step = 0
        self.best_val_loss = float("inf")
        self.best_bleu = 0.0
        self.best_wer = float("inf")

        logger.info("Initialization complete")

    def train_step(self, batch):
        audio = batch["audio"].to(config.device)
        texts = batch["text"]
        try:
            audio_inputs = self.processor(
                audio=audio.cpu().numpy(),
                return_tensors="pt",
                sampling_rate=config.sample_rate,
            )
            audio_inputs = {k: v.to(config.device) for k, v in audio_inputs.items() if isinstance(v, torch.Tensor)}

            text_inputs = self.processor.tokenizer(
                texts, return_tensors="pt", padding=True, truncation=True, max_length=100
            )
            labels = text_inputs["input_ids"].to(config.device)

            outputs = self.model(**audio_inputs, labels=labels)
            loss = outputs.loss

            loss = loss / config.gradient_accumulation_steps
            loss.backward()

            return float(loss.item() * config.gradient_accumulation_steps)
        except Exception as e:
            logger.error(f"Train step error: {e}", exc_info=True)
            return 0.0

    @torch.no_grad()
    def validate(self):
        logger.info("-" * 70)
        logger.info(f"Validation - Step {self.global_step}")
        self.model.eval()

        losses = []
        all_refs = []
        all_hyps = []
        failed_batches = 0
        successful_batches = 0

        for batch_idx, batch in enumerate(tqdm(self.val_loader, desc="Validating")):
            try:
                audio = batch["audio"].to(config.device)
                texts = batch["text"]

                audio_inputs = self.processor(
                    audio=audio.cpu().numpy(),
                    return_tensors="pt",
                    sampling_rate=config.sample_rate,
                )
                audio_inputs = {k: v.to(config.device) for k, v in audio_inputs.items() if isinstance(v, torch.Tensor)}

                text_inputs = self.processor.tokenizer(
                    texts, return_tensors="pt", padding=True, truncation=True, max_length=100
                )
                labels = text_inputs["input_ids"].to(config.device)

                outputs = self.model(**audio_inputs, labels=labels)
                losses.append(float(outputs.loss.item()))

                # Ensure tgt_lang specified and generate_speech explicitly False
                gen_outputs = None
                try:
                    gen_outputs = self.model.generate(
                        **audio_inputs,
                        tgt_lang=config.target_lang,
                        generate_speech=False,
                        max_new_tokens=50,
                        num_beams=3,
                    )
                except Exception as ge:
                    # Log and continue (do not crash validation loop)
                    logger.warning(f"Generation error on batch {batch_idx}: {ge}")
                    failed_batches += 1
                    continue

                # Extract token ids robustly
                if isinstance(gen_outputs, tuple):
                    generated_ids = gen_outputs[0]
                elif hasattr(gen_outputs, "sequences"):
                    generated_ids = gen_outputs.sequences
                else:
                    generated_ids = gen_outputs

                if isinstance(generated_ids, torch.Tensor):
                    if generated_ids.ndim == 3:
                        generated_ids = generated_ids[:, 0, :]
                else:
                    logger.warning(f"Generated ids unexpected type: {type(generated_ids)}")
                    failed_batches += 1
                    continue

                translations = self.processor.batch_decode(generated_ids, skip_special_tokens=True)
                translations = [t.strip() for t in translations]

                all_refs.extend(texts)
                all_hyps.extend(translations)
                successful_batches += 1

            except Exception as e:
                failed_batches += 1
                logger.warning(f"Val batch {batch_idx} error: {e}", exc_info=True)

        if not losses:
            self.model.train()
            logger.warning("No validation loss recorded")
            return float("inf"), 0.0, 1.0

        avg_loss = sum(losses) / len(losses)
        bleu = calculate_bleu(all_refs, all_hyps)
        wer = calculate_wer(all_refs, all_hyps)

        logger.info(f"Validation results: Loss={avg_loss:.4f}, BLEU={bleu:.2f}, WER={wer:.4f}")
        logger.info(f"Successful batches: {successful_batches}/{len(self.val_loader)}; Failed: {failed_batches}")

        # Save best checkpoints
        improved = False
        if avg_loss < self.best_val_loss:
            self.best_val_loss = avg_loss
            self.save_checkpoint("loss")
            improved = True

        if bleu > self.best_bleu:
            self.best_bleu = bleu
            self.save_checkpoint("bleu")
            improved = True

        if wer < self.best_wer:
            self.best_wer = wer
            self.save_checkpoint("wer")
            improved = True

        self.model.train()
        return avg_loss, bleu, wer

    def save_checkpoint(self, metric):
        save_dir = Path(config.checkpoints_dir) / f"best_{metric}"
        save_dir.mkdir(exist_ok=True, parents=True)
        self.model.save_pretrained(save_dir)
        results = {
            "ablation": "baseline",
            "date": datetime.now().strftime("%Y-%m-%d %H:%M:%S UTC"),
            "best_val_loss": float(self.best_val_loss),
            "best_bleu": float(self.best_bleu),
            "best_wer": float(self.best_wer),
            "global_step": self.global_step,
        }
        with open(save_dir / "results.json", "w") as f:
            json.dump(results, f, indent=2)
        logger.info(f"Saved checkpoint for {metric} at {save_dir}")

    def train(self):
        logger.info("TRAINING START")
        logger.info(f"Epochs={config.num_epochs}, Batch size={config.batch_size}, Gradient accumulation={config.gradient_accumulation_steps}")
        for epoch in range(config.num_epochs):
            logger.info(f"Epoch {epoch+1}/{config.num_epochs}")
            progress = tqdm(self.train_loader, desc=f"Epoch {epoch+1}")
            losses = []
            for step, batch in enumerate(progress):
                loss = self.train_step(batch)
                losses.append(loss)

                if (step + 1) % config.gradient_accumulation_steps == 0:
                    torch.nn.utils.clip_grad_norm_(self.model.parameters(), config.max_grad_norm)
                    self.optimizer.step()
                    self.scheduler.step()
                    self.optimizer.zero_grad()
                    self.global_step += 1
                    if self.global_step % config.clear_cache_steps == 0:
                        torch.cuda.empty_cache()

                avg = sum(losses[-10:]) / min(10, len(losses))
                progress.set_postfix({"loss": f"{avg:.4f}"})

                if self.global_step > 0 and self.global_step % config.eval_steps == 0:
                    self.validate()

            epoch_loss = sum(losses) / len(losses) if losses else 0.0
            logger.info(f"Epoch {epoch+1} complete - Avg Loss: {epoch_loss:.4f}")
            # Run validation at epoch end
            self.validate()

        logger.info("TRAINING COMPLETE")
        logger.info(f"Best Loss: {self.best_val_loss:.4f} | Best BLEU: {self.best_bleu:.2f} | Best WER: {self.best_wer:.4f}")

In [ ]:
torch.manual_seed(config.seed)
if torch.cuda.is_available():
    torch.cuda.manual_seed_all(config.seed)
    logger.info(f"Using GPU: {torch.cuda.get_device_name(0)}")
else:
    logger.info("Using CPU")

trainer = BaselineTrainer()
trainer.train()

2025-11-16 11:41:20,816 [INFO] Using GPU: NVIDIA GeForce RTX 3060
2025-11-16 11:41:20,816 [INFO] Loading models...
2025-11-16 11:41:20,816 [INFO] 
Loading models...


`torch_dtype` is deprecated! Use `dtype` instead!
Instantiating a decoder SeamlessM4Tv2Attention without passing `layer_idx` is not recommended and will lead to errors during the forward call, if caching is used. Please make sure to provide a `layer_idx` when creating this class.


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

2025-11-16 11:41:46,311 [INFO]   S2S Trainable: 53,870,592 / 2,363,120,261 (2.28%)
2025-11-16 11:41:46,347 [INFO] Loading ASR model for back-translation...
2025-11-16 11:41:54,812 [INFO] ASR model loaded successfully
2025-11-16 11:41:54,812 [INFO] Loading semantic similarity model...
2025-11-16 11:41:54,828 [INFO] Use pytorch device_name: cuda:0
2025-11-16 11:41:54,828 [INFO] Load pretrained SentenceTransformer: sentence-transformers/paraphrase-multilingual-mpnet-base-v2
2025-11-16 11:42:02,695 [INFO] Semantic model loaded successfully
2025-11-16 11:42:02,748 [INFO] Models loaded and moved to device
2025-11-16 11:42:02,748 [INFO] Creating datasets and dataloaders...
2025-11-16 11:42:03,845 [INFO]   1507 files → 3371 chunks (all)
2025-11-16 11:42:03,865 [INFO]   50 files → 98 chunks (dev)
2025-11-16 11:42:03,865 [INFO] Limiting val samples to 50
2025-11-16 11:42:03,865 [INFO] Train batches: 3371
2025-11-16 11:42:03,865 [INFO] Val batches: 98
2025-11-16 11:42:03,865 [INFO] Setting up opt

Epoch 1:   0%|          | 0/3371 [00:00<?, ?it/s]

...

2025-11-16 16:03:47,906 [INFO] Epoch 5 complete - Avg Loss: 2.5040
2025-11-16 16:03:47,906 [INFO] ----------------------------------------------------------------------
2025-11-16 16:03:47,906 [INFO] Validation - Step 1050


Validating:   0%|          | 0/98 [00:00<?, ?it/s]

The `use_cache` argument is changed to `False` since `labels` is provided.
This calls the same method `forward` as `SeamlessM4Tv2ForTextToText` and `SeamlessM4Tv2ForSpeechToText`depending on the input modality. If you want to generate speech, use the `generate` method.
The `use_cache` argument is changed to `False` since `labels` is provided.
This calls the same method `forward` as `SeamlessM4Tv2ForTextToText` and `SeamlessM4Tv2ForSpeechToText`depending on the input modality. If you want to generate speech, use the `generate` method.
The `use_cache` argument is changed to `False` since `labels` is provided.
This calls the same method `forward` as `SeamlessM4Tv2ForTextToText` and `SeamlessM4Tv2ForSpeechToText`depending on the input modality. If you want to generate speech, use the `generate` method.
The `use_cache` argument is changed to `False` since `labels` is provided.
This calls the same method `forward` as `SeamlessM4Tv2ForTextToText` and `SeamlessM4Tv2ForSpeechToText`depending on

2025-11-16 16:05:02,546 [INFO] Validation results: Loss=2.0483, BLEU=42.73, WER=0.7589
2025-11-16 16:05:02,546 [INFO] Successful batches: 98/98; Failed: 0
2025-11-16 16:05:03,684 [INFO] Saved checkpoint for loss at baseline_ablation\checkpoints\best_loss
2025-11-16 16:05:03,709 [INFO] TRAINING COMPLETE
2025-11-16 16:05:03,711 [INFO] Best Loss: 2.0483 | Best BLEU: 42.73 | Best WER: 0.7440


: 